In [265]:
import pandas as pd
import gurobipy as gp
import math
import pickle as pkl
from datetime import datetime, timedelta


In [266]:
product_type = "frozen"
num_time_periods = 365

In [267]:
article_data = pd.read_csv("./data/article.csv")
article_data = article_data[(article_data['TEMPERATURE_ZONE'] == product_type)]

In [268]:
# constants definitions
if(product_type=="frozen"):
    warehouse_volume = 50
if(product_type=="chilled"):
    warehouse_volume = 300
if(product_type=="ambient"):
    warehouse_volume = 900
buffer_cost = 25
default_max_order = 10000

In [269]:
def createParameterMatrix(data, columns):
    parameters = []
    for column in columns:
        parameters.append(data[column].to_list())
    parameters = list(map(list, zip(*parameters)))
    return parameters

In [270]:
articles = article_data['ARTICLE_ID'].to_list()

parameters = createParameterMatrix(
    article_data,
    [
        'TEMPERATURE_ZONE',
        'VOLUME_M3_PER_CU',
        'MEAN_SHELF_LIFE',
        'CU_PER_TU',
        'ORDERING_COST_FIXED',
        'ORDERING_COST_PER_TU',
        'CLEARING_COST_PER_CU',
        'MINIMUM_ORDER_QUANTITY_TU',
        'MAXIMUM_ORDER_QUANTITY_TU'
    ]
)
parameters_dict = dict(zip(articles, parameters))

In [271]:
items, category, volume_per_cu, shelf_life, cu_per_tu, ordering_cost_fixed, ordering_cost_per_tu, clearing_cost_per_cu,minimum_order_quantity_tu, maximum_order_quantity_tu = gp.multidict(parameters_dict)

In [272]:
forecast_data = pd.read_csv('./data/sales_'+str(num_time_periods)+'.csv')
forecast_data = forecast_data[forecast_data['ARTICLE_ID'].isin(articles)]

In [273]:
# Create a new dataframe with all dates
all_dates_df = pd.DataFrame({'DATE': pd.date_range(start='2022-01-01', end='2022-12-31')})

# Group the original dataframe by item
grouped = forecast_data.groupby('ARTICLE_ID')

# Initialize an empty list to store the new dataframes
new_dfs = []

# Loop over each group
for item, group_df in grouped:
    
    group_df['DATE'] = pd.to_datetime(group_df['DATE'])

    # Merge the group dataframe with the all_dates dataframe
    merged_df = pd.merge(all_dates_df, group_df, on='DATE', how='outer')
    merged_df['ARTICLE_ID'] = item
    
    # Fill in missing values
    merged_df['PICKING_QUANTITY_CU'] = merged_df['PICKING_QUANTITY_CU'].fillna(0)
    
    # Sort by date and append to the list
    new_dfs.append(merged_df.sort_values('DATE'))
    
# Concatenate all new dataframes into a single dataframe
forecast_data = pd.concat(new_dfs)
forecast_data


DATE ARTICLE_ID  PICKING_QUANTITY_CU
0   2022-01-01   00ee8964                  0.0
1   2022-01-02   00ee8964                  0.0
2   2022-01-03   00ee8964                  8.0
3   2022-01-04   00ee8964                  4.0
4   2022-01-05   00ee8964                  8.0
..         ...        ...                  ...
360 2022-12-27   ffc3d18a                  6.0
361 2022-12-28   ffc3d18a                  1.0
362 2022-12-29   ffc3d18a                  2.0
363 2022-12-30   ffc3d18a                  4.0
364 2022-12-31   ffc3d18a                  1.0

[152935 rows x 3 columns]

In [274]:
# # Create a MultiIndex with 'item' and 'date'
# idx = pd.MultiIndex.from_product([forecast_data['ARTICLE_ID'].unique(), pd.date_range('2022-01-01', '2022-12-31', freq='D')], names=['ARTICLE_ID', 'DATE'])

# print(forecast_data)
# # Set the DataFrame index to the MultiIndex
# forecast_data = forecast_data.set_index(['ARTICLE_ID', 'DATE'])
# print(forecast_data)

# # Reindex the DataFrame with the new MultiIndex and fill missing values with 0
# forecast_data = forecast_data.reindex(idx)
# print(forecast_data)

# # Reset the index to make 'item' and 'date' columns again
# forecast_data = forecast_data.reset_index().astype({"DATE": str})

time_periods = forecast_data['DATE'].unique()


In [275]:
demand = forecast_data.groupby('ARTICLE_ID').apply(lambda x: dict(zip(x['DATE'], x['PICKING_QUANTITY_CU']))).to_dict()
demand

{'00ee8964': {Timestamp('2022-01-01 00:00:00'): 0.0,
  Timestamp('2022-01-02 00:00:00'): 0.0,
  Timestamp('2022-01-03 00:00:00'): 8.0,
  Timestamp('2022-01-04 00:00:00'): 4.0,
  Timestamp('2022-01-05 00:00:00'): 8.0,
  Timestamp('2022-01-06 00:00:00'): 7.0,
  Timestamp('2022-01-07 00:00:00'): 9.0,
  Timestamp('2022-01-08 00:00:00'): 8.0,
  Timestamp('2022-01-09 00:00:00'): 0.0,
  Timestamp('2022-01-10 00:00:00'): 4.0,
  Timestamp('2022-01-11 00:00:00'): 5.0,
  Timestamp('2022-01-12 00:00:00'): 6.0,
  Timestamp('2022-01-13 00:00:00'): 3.0,
  Timestamp('2022-01-14 00:00:00'): 11.0,
  Timestamp('2022-01-15 00:00:00'): 8.0,
  Timestamp('2022-01-16 00:00:00'): 0.0,
  Timestamp('2022-01-17 00:00:00'): 4.0,
  Timestamp('2022-01-18 00:00:00'): 4.0,
  Timestamp('2022-01-19 00:00:00'): 1.0,
  Timestamp('2022-01-20 00:00:00'): 3.0,
  Timestamp('2022-01-21 00:00:00'): 4.0,
  Timestamp('2022-01-22 00:00:00'): 3.0,
  Timestamp('2022-01-23 00:00:00'): 0.0,
  Timestamp('2022-01-24 00:00:00'): 8.0,
  T

In [276]:
# model object
m = gp.Model()

# decision variables
# Xit
orders = m.addVars(items, time_periods, vtype=gp.GRB.INTEGER, lb=0)
# Yit
ordered_boolean = m.addVars(items, time_periods, vtype=gp.GRB.BINARY, lb=0)
# Sit
storage_used = m.addVars(items, time_periods, vtype=gp.GRB.INTEGER, lb=0)
# Zt
buffer_storage_used = m.addVars(time_periods, vtype=gp.GRB.INTEGER, lb=0)

# objective function
ordering_cost_per_tu_objective = gp.quicksum(ordering_cost_per_tu[item] * orders[item, time_period] for item in items for time_period in time_periods)
ordering_cost_fixed_objective = gp.quicksum(ordering_cost_fixed[item] * ordered_boolean[item, time_period] for item in items for time_period in time_periods)
buffer_storage_objective = gp.quicksum(buffer_cost * buffer_storage_used[time_period] for time_period in time_periods)

m.setObjective(ordering_cost_per_tu_objective + ordering_cost_fixed_objective + buffer_storage_objective, sense=gp.GRB.MINIMIZE)

# constraints
# demand satisfaction
for item in items:
    for time_period_iterator, time_period in enumerate(time_periods):
        if(time_period_iterator==0):
            m.addConstr(orders[item, time_period] * cu_per_tu[item] >= demand[item][time_period],name="demand constraint_" + str(time_period))
        else:
            m.addConstr((orders[item, time_period] * cu_per_tu[item]) + storage_used[item, time_periods[time_period_iterator-1]] >= demand[item][time_period],name="demand constraint_" + str(time_period))

# inventory volume constraint
for time_period_iterator, time_period in enumerate(time_periods):
    if(time_period_iterator==0):
        m.addConstr(gp.quicksum(volume_per_cu[item] * ((cu_per_tu[item] * (orders[item, time_period]))) for item in items) <= warehouse_volume + buffer_storage_used[time_period])
    else:
        m.addConstr(gp.quicksum(volume_per_cu[item] * (storage_used[item, time_periods[time_period_iterator-1]] + (cu_per_tu[item] * (orders[item, time_period]))) for item in items) <= warehouse_volume + buffer_storage_used[time_period])

# # min/max constraints (linking too)
for item in items:
    for time_period in time_periods:
        m.addConstr(orders[item, time_period] >= minimum_order_quantity_tu[item] * ordered_boolean[item, time_period])
        # if((not math.isnan(maximum_order_quantity_tu[item]))):
        #     m.addConstr(orders[item, time_period] <= maximum_order_quantity_tu[item] * ordered_boolean[item, time_period])
        # else:
        #     m.addConstr(orders[item, time_period] <= default_max_order * ordered_boolean[item, time_period])

# current inventory constraint
for item in items:
    for time_period_iterator,time_period in enumerate(time_periods):
        if(time_period_iterator==0):
            m.addConstr(storage_used[item, time_periods[time_period_iterator]] == (orders[item, time_period] * cu_per_tu[item]) - demand[item][time_period])
        else:
            m.addConstr(storage_used[item, time_periods[time_period_iterator]] == storage_used[item, time_periods[time_period_iterator-1]] + (orders[item, time_period] * cu_per_tu[item]) - demand[item][time_period])

m.setParam(gp.GRB.Param.Heuristics, 0) 
m.optimize()

Set parameter Heuristics to value 0
Gurobi Optimizer version 10.0.1 build v10.0.1rc0 (win64)

CPU model: AMD Ryzen 7 5800U with Radeon Graphics, instruction set [SSE2|AVX|AVX2]
Thread count: 8 physical cores, 16 logical processors, using up to 16 threads

Optimize a model with 459170 rows, 459170 columns and 1242663 nonzeros
Model fingerprint: 0xbbbbb382
Variable types: 0 continuous, 459170 integer (152935 binary)
Coefficient statistics:
  Matrix range     [2e-04, 2e+01]
  Objective range  [1e-01, 3e+01]
  Bounds range     [1e+00, 1e+00]
  RHS range        [1e+00, 4e+02]
Presolve removed 372484 rows and 320434 columns
Presolve time: 3.76s
Presolved: 86686 rows, 138736 columns, 479650 nonzeros
Variable types: 0 continuous, 138736 integer (190 binary)
Deterministic concurrent LP optimizer: primal and dual simplex
Showing first log only...

Concurrent spin time: 0.06s

Solved with primal simplex

Root relaxation: objective 2.688562e+05, 655 iterations, 0.73 seconds (0.51 work units)

    